In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Obstructive_sleep_apnea"
cohort = "GSE135917"

# Input paths
in_trait_dir = "../../input/GEO/Obstructive_sleep_apnea"
in_cohort_dir = "../../input/GEO/Obstructive_sleep_apnea/GSE135917"

# Output paths
out_data_file = "../../output/preprocess/Obstructive_sleep_apnea/GSE135917.csv"
out_gene_data_file = "../../output/preprocess/Obstructive_sleep_apnea/gene_data/GSE135917.csv"
out_clinical_data_file = "../../output/preprocess/Obstructive_sleep_apnea/clinical_data/GSE135917.csv"
json_path = "../../output/preprocess/Obstructive_sleep_apnea/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Subcutaneous fat transcriptome in obstructive sleep apnea and after treatment with CPAP"
!Series_summary	"Obstructive sleep apnea (OSA) has been linked to dysregulated metabolic states and treatment of sleep apnea may improve these conditions. Subcutaneous adipose tissue is a readily samplable fat depot that plays an important role in regulating metabolism. However, neither the pathophysiologic consequences of OSA nor the effects of continuous positive airway pressure (CPAP) in altering this compartment’s molecular pathways are understood. This study aimed to systematically identify subcutaneous adipose tissue transcriptional programs modulated in OSA and in response to its effective treatment with CPAP.  Two subject groups were investigated: Study Group 1 was comprised of 10 OSA and 8 controls; Study Group 2 included 24 individuals with OSA studied at baseline and following CPAP. For each subject, genome-wide gene expression measurement of subcut

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
# 1. Gene Expression Data Availability
# Based on the background information, this is a microarray study using GeneChip Human Gene 1.0 ST
# Affymetrix microarray, which measures genome-wide gene expression.
is_gene_available = True

# 2. Variable Availability and Data Type Conversion
# 2.1 Data Availability

# For trait (Obstructive_sleep_apnea):
# The study specifically investigates OSA vs controls and OSA before vs after CPAP treatment.
# While there isn't a direct key in the sample characteristics dictionary that indicates OSA status,
# the background information confirms this dataset is about OSA.
# However, without information to differentiate which samples are OSA vs controls, or before vs after
# treatment, we cannot create a proper binary or continuous variable for the trait.
trait_row = None

# For age:
# Age is available at index 0
age_row = 0

# For gender:
# Gender is available at index 1 as 'Sex'
gender_row = 1

# 2.2 Data Type Conversion Functions

# Since trait data is not directly available in the provided sample characteristics,
# we define a placeholder function
def convert_trait(value):
    return None

# Age conversion: continuous variable
def convert_age(value):
    try:
        # Extract the value after colon and strip any whitespace
        age_str = value.split(':', 1)[1].strip()
        return float(age_str)
    except (ValueError, IndexError, AttributeError):
        return None

# Gender conversion: binary variable (0 for female, 1 for male)
def convert_gender(value):
    try:
        # Extract the value after colon and strip any whitespace
        gender_str = value.split(':', 1)[1].strip().upper()
        if gender_str == 'F':
            return 0  # Female
        elif gender_str == 'M':
            return 1  # Male
        else:
            return None
    except (IndexError, AttributeError):
        return None

# 3. Save Metadata
# While this study is about OSA, we don't have enough information in the provided
# sample characteristics to determine the OSA status of each sample.
# Additional metadata would be needed to properly use this dataset.
is_trait_available = trait_row is not None
validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
# Skip this substep since trait_row is None (clinical data for the trait is not available in the provided sample characteristics)


False

### Step 3: Gene Data Extraction

In [4]:
# 1. Re-identify the SOFT and matrix files to ensure we have the correct paths
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Extract the gene expression data from the matrix file
gene_data = get_genetic_data(matrix_file)

# 3. Print the first 20 row IDs (gene or probe identifiers)
print("\nFirst 20 gene/probe identifiers:")
print(gene_data.index[:20])

# 4. Print the dimensions of the gene expression data
print(f"\nGene data dimensions: {gene_data.shape[0]} genes × {gene_data.shape[1]} samples")

# Note: we keep is_gene_available as True since we successfully extracted gene expression data
is_gene_available = True



First 20 gene/probe identifiers:
Index(['7892501', '7892502', '7892503', '7892504', '7892505', '7892506',
       '7892507', '7892508', '7892509', '7892510', '7892511', '7892512',
       '7892513', '7892514', '7892515', '7892516', '7892517', '7892518',
       '7892519', '7892520'],
      dtype='object', name='ID')

Gene data dimensions: 33297 genes × 66 samples


### Step 4: Gene Identifier Review

In [5]:
# Looking at the gene identifiers from the previous step

# These identifiers appear to be probe IDs (7892501, 7892502, etc.) from a microarray platform
# rather than standard human gene symbols (which would look like BRCA1, TP53, etc.)

# These numeric IDs are likely platform-specific microarray probe identifiers that need to be 
# mapped to standard gene symbols for biological interpretation

# Based on the format (7-digit numeric IDs), these appear to be Illumina BeadArray probe IDs
# which require mapping to standard gene symbols

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. First get the file paths using geo_get_relevant_filepaths function
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 3. Use the 'preview_df' function from the library to preview the data and print out the results.
print("Gene annotation preview:")
print(preview_df(gene_annotation))


Gene annotation preview:
{'ID': ['7896736', '7896738', '7896740', '7896742', '7896744'], 'GB_LIST': [nan, nan, 'NM_001004195,NM_001005240,NM_001005484,BC136848,BC136867,BC136907,BC136908', 'NR_024437,XM_006711854,XM_006726377,XR_430662,AK298283,AL137655,BC032332,BC118988,BC122537,BC131690,NM_207366,AK301928,BC071667', 'NM_001005221,NM_001005224,NM_001005277,NM_001005504,BC137547,BC137568'], 'SPOT_ID': ['chr1:53049-54936', 'chr1:63015-63887', 'chr1:69091-70008', 'chr1:334129-334296', 'chr1:367659-368597'], 'seqname': ['chr1', 'chr1', 'chr1', 'chr1', 'chr1'], 'RANGE_GB': ['NC_000001.10', 'NC_000001.10', 'NC_000001.10', 'NC_000001.10', 'NC_000001.10'], 'RANGE_STRAND': ['+', '+', '+', '+', '+'], 'RANGE_START': ['53049', '63015', '69091', '334129', '367659'], 'RANGE_STOP': ['54936', '63887', '70008', '334296', '368597'], 'total_probes': [7.0, 31.0, 24.0, 6.0, 36.0], 'gene_assignment': ['---', 'ENST00000328113 // OR4G2P // olfactory receptor, family 4, subfamily G, member 2 pseudogene // ---

### Step 6: Gene Identifier Mapping

In [7]:
# 1. Identify the columns for gene ID mapping
# From the gene annotation preview, we can see that the 'ID' column contains the probe identifiers
# which match the identifiers in the gene expression data (e.g., 7896736, 7896738)
# The 'gene_assignment' column contains the gene symbols and annotations

# 2. Get a gene mapping dataframe by extracting the relevant columns
prob_col = 'ID'
gene_col = 'gene_assignment'
gene_mapping = get_gene_mapping(gene_annotation, prob_col, gene_col)

# 3. Apply the gene mapping to convert probe-level measurements to gene expression data
gene_data = apply_gene_mapping(gene_data, gene_mapping)

# 4. Print dimensions and preview of the mapped gene expression data
print(f"\nMapped gene data dimensions: {gene_data.shape[0]} genes × {gene_data.shape[1]} samples")
print("\nPreview of mapped gene data (first 5 genes):")
print(gene_data.head())

# 5. Normalize gene symbols to handle synonyms using the built-in function
gene_data = normalize_gene_symbols_in_index(gene_data)
print(f"\nAfter normalization: {gene_data.shape[0]} genes × {gene_data.shape[1]} samples")



Mapped gene data dimensions: 117474 genes × 66 samples

Preview of mapped gene data (first 5 genes):
      GSM4037879  GSM4037880  GSM4037881  GSM4037882  GSM4037883  GSM4037884  \
Gene                                                                           
A-     38.515107   37.633482   38.035349   38.102504   38.303999   39.273446   
A-3-    0.997671    0.924286    0.933457    0.945234    0.920517    0.919650   
A-52    1.480764    1.481651    1.561904    1.516093    1.500459    1.530657   
A-E     1.528866    1.495562    1.488930    1.507266    1.541892    1.561942   
A-I     2.439798    2.401892    2.434683    2.424852    2.437168    2.427981   

      GSM4037885  GSM4037886  GSM4037887  GSM4037888  ...  GSM4037935  \
Gene                                                  ...               
A-     40.008071   38.404476   37.834512   39.434636  ...   36.845383   
A-3-    1.024126    0.917176    0.994991    0.988070  ...    1.006340   
A-52    1.392436    1.531903    1.496287    1

### Step 7: Data Normalization and Linking

In [8]:
# 1. The gene data processing and normalization worked well
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)
gene_data = get_genetic_data(matrix_file)

# Extract gene annotation data for mapping
gene_annotation = get_gene_annotation(soft_file)
gene_mapping = get_gene_mapping(gene_annotation, prob_col='ID', gene_col='gene_assignment')

# Apply gene mapping to convert probe-level data to gene expression data
gene_data = apply_gene_mapping(gene_data, gene_mapping)

# Normalize gene symbols in the gene expression data
print("Normalizing gene symbols...")
normalized_gene_data = normalize_gene_symbols_in_index(gene_data)
print(f"Gene data shape after normalization: {normalized_gene_data.shape}")
print(f"First 5 normalized gene symbols: {normalized_gene_data.index[:5].tolist()}")

# Save the normalized gene data
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
normalized_gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# 2. Re-examine the dataset background to understand the structure
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

print("\nBackground information:")
print(background_info)

print("\nSample characteristics:")
sample_characteristics_dict = get_unique_values_by_row(clinical_data)
print(sample_characteristics_dict)

# From the background information, this dataset contains samples from two study designs:
# 1) 10 OSA vs 8 controls
# 2) 24 OSA at baseline vs after CPAP
# However, the sample characteristics do not explicitly contain this labeling info

# 3. Based on the review, we don't have trait (OSA status or treatment status) information 
# in the sample characteristics, so we cannot extract it directly
is_trait_available = False
is_gene_available = True

# Create a dummy dataframe with the trait column to satisfy the validation function
dummy_df = pd.DataFrame({trait: [float('nan')]})

# 4. Write the final status of this cohort to the JSON file
is_usable = validate_and_save_cohort_info(
    is_final=False,  # Set to False since we can't do a complete final validation
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 5. Don't save linked data since trait information is not available
print("Dataset lacks trait information needed for association studies, linked data not saved.")

Normalizing gene symbols...
Gene data shape after normalization: (24229, 66)
First 5 normalized gene symbols: ['A1BG', 'A1CF', 'A2M', 'A2ML1', 'A3GALT2']


Normalized gene data saved to ../../output/preprocess/Obstructive_sleep_apnea/gene_data/GSE135917.csv

Background information:
!Series_title	"Subcutaneous fat transcriptome in obstructive sleep apnea and after treatment with CPAP"
!Series_summary	"Obstructive sleep apnea (OSA) has been linked to dysregulated metabolic states and treatment of sleep apnea may improve these conditions. Subcutaneous adipose tissue is a readily samplable fat depot that plays an important role in regulating metabolism. However, neither the pathophysiologic consequences of OSA nor the effects of continuous positive airway pressure (CPAP) in altering this compartment’s molecular pathways are understood. This study aimed to systematically identify subcutaneous adipose tissue transcriptional programs modulated in OSA and in response to its effective treatment with CPAP.  Two subject groups were investigated: Study Group 1 was comprised of 10 OSA and 8 controls; Study Group 2 included 24 individuals with OSA stud